In [9]:
import pandas as pd
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import word_tokenize
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import pickle
import re


In [10]:
buisness = pd.read_csv("processed_hotels.csv")
buisness.columns

C:\Users\mohan\AppData\Local\Temp\ipykernel_14836\3508771870.py:1: DtypeWarning: Columns (20,22,24,27,29,30,32,34,36,38,39,42,45,46,47) have mixed types. Specify dtype option on import or set low_memory=False.
  buisness = pd.read_csv("processed_hotels.csv")


Index(['business_id', 'name', 'address', 'City', 'State', 'postal_code',
       'latitude', 'longitude', 'stars', 'review_count', 'is_open',
       'attributes', 'categories', 'hours', 'value', 'BusinessParking',
       'Ambience', 'GoodForMeal', 'Dietary', 'Music', 'ByAppointmentOnly',
       'BusinessAcceptsCreditCards', 'BikeParking', 'RestaurantsPriceRange2',
       'CoatCheck', 'RestaurantsTakeOut', 'RestaurantsDelivery', 'Caters',
       'WiFi', 'WheelchairAccessible', 'HappyHour', 'OutdoorSeating', 'HasTV',
       'RestaurantsReservations', 'DogsAllowed', 'Alcohol', 'GoodForKids',
       'RestaurantsAttire', 'RestaurantsTableService',
       'RestaurantsGoodForGroups', 'DriveThru', 'NoiseLevel',
       'BusinessAcceptsBitcoin', 'Smoking', 'GoodForDancing',
       'AcceptsInsurance', 'BYOB', 'Corkage', 'BYOBCorkage',
       'RestaurantsCounterService', 'Open24Hours', 'AgesAllowed', 'BestNights',
       'HairSpecializesIn', 'DietaryRestrictions', 'garage', 'street',
       'valida

In [11]:
# Sum all the categories in the city and use it for content based filtering
inp = buisness[["categories","City"]].groupby("City").sum()
cities = inp.index
values = inp.values


In [12]:
cities

Index(['AVON', 'Abington', 'Abington Township', 'Affton', 'Aldan', 'Algiers',
       'Aliso Viejo', 'Alloway', 'Almonesson', 'Alton',
       ...
       'sewell', 'sparks', 'spring city', 'tampa', 'telford', 'tucson',
       'wilmington', 'wimauma', '​Clayton', '​Largo'],
      dtype='object', name='City', length=1083)

In [13]:
new_values = []
for v in values:
    new_values.append(v[0])

In [14]:
new_values

['Coffee & Tea, Food, Donuts, Pretzels',
 "Digitizing Services, Hotels & Travel, Photography Stores & Services, Shopping, Passport & Visa Services, Local Services, Printing Services, Travel Services, Professional ServicesThai, RestaurantsSteakhouses, Restaurants, Japanese, Sushi BarsPest Control, Local ServicesShopping, Home & Garden, Interior Design, Home Decor, Furniture Stores, Home ServicesBarbeque, RestaurantsLocal Services, Appliances & RepairThai, RestaurantsMexican, Restaurants, Fast FoodChicken Wings, Pizza, RestaurantsDelis, Restaurants, Coffee & Tea, Food, Breakfast & Brunch, Bagels, SandwichesBike Rentals, Auto Repair, Oil Change Stations, Tires, Active Life, AutomotiveFood, Coffee & TeaEvent Planning & Services, Diners, Gluten-Free, Restaurants, American (Traditional), Venues & Event SpacesRestaurants, Trinidadian, CaribbeanRestaurants, Soup, SandwichesSandwiches, Coffee & Tea, Restaurants, Food, Delis, Breakfast & Brunch, BagelsLaundry Services, Local Services, Dry Cleani

In [15]:
StopWords = set(stopwords.words("english")) 
lemmatizer = WordNetLemmatizer()
def clean_text(text):

    text = text.lower()

    text = re.sub("\([^+]*\)","",text)       # Removing any values with in the ()
    text = re.sub("\d","",text)              # Removing digits
    text = re.sub("\s[a-zA-Z]\s"," ",text)  # Removing single alphabets
    text = re.sub("\[[^+]*\]","",text)     # Removing squate brackets and the content inside it
    text = re.sub("[#-]+","",text)         # Removing hashtags and -  
    text = re.sub("\n","",text)            # Removing newlines 
    text = re.sub("\s\s+"," ",text)         #removing More then one spaces

    text = word_tokenize(text)

    text = [ lemmatizer.lemmatize(word) for word in text if word not in StopWords and len(word)>2]
    
    return " ".join(text)

processed_values = [clean_text(txt) for txt in new_values]

In [16]:
processed_values[:5]

['coffee tea food donut pretzel',
 'digitizing service hotel travel photography store service shopping passport visa service local service printing service travel service professional servicesthai restaurantssteakhouses restaurant japanese sushi barspest control local servicesshopping home garden interior design home decor furniture store home servicesbarbeque restaurantslocal service appliance repairthai restaurantsmexican restaurant fast foodchicken wing pizza restaurantsdelis restaurant coffee tea food breakfast brunch bagel sandwichesbike rental auto repair oil change station tire active life automotivefood coffee teaevent planning service diner glutenfree restaurant american tax service accountant professional service financial servicesshades blind home service interior designmassage therapy acupuncture health medical professional service chiropractorsbeer wine spirit food restaurant delisrestaurants cajun/creole seafoodfuneral service cemetery local servicesrestaurants mexicanfoo

In [17]:
TFIDF = TfidfVectorizer(stop_words="english")
categories = TFIDF.fit_transform(processed_values)
categories

<1083x4193 sparse matrix of type '<class 'numpy.float64'>'
	with 31055 stored elements in Compressed Sparse Row format>

In [18]:
cossim = cosine_similarity(categories,categories)

In [19]:
reverse_index = dict()

for i,name in enumerate(cities):
    reverse_index[name] = i

In [20]:
def get_similar_cities(city_name , cos_sim = cossim):

    indx = reverse_index[city_name]

    get_similar_cities = list(enumerate(cos_sim[indx]))

    get_similar_cities = sorted(get_similar_cities ,key = lambda x : x[1], reverse=True)

    get_similar_cities = get_similar_cities[1:11]
    
    city_indices =  [i for i,j in get_similar_cities]

    return [cities[i] for i in city_indices][1:]

In [23]:
get_similar_cities("Montgomeryville")

['Manchester',
 'Santa  Barbara',
 'Tampa - North',
 'Earth City',
 'Doylestown',
 'Brentwood - Cool Springs',
 'Willow Grove',
 'Tampa - South',
 'Salinas']

In [4]:
#content_filttering = dict()
#
#content_filttering["cities"] = cities
#content_filttering["reverse_indices"] = reverse_index
#content_filttering["cossim"] = cossim#

#pickle.dump(content_filttering , open("content_filttering.pkl", "wb"))

In [5]:
#pickle.load(open("content_filttering.pkl","rb"))

In [3]:
import pandas as pd

In [1]:
from Filtering import collabrative_filtering

city_recom = collabrative_filtering()

In [14]:
similar_cities = city_recom.get_similar_cities("Manchester")
similar_cities

['Santa  Barbara', 'Telford', 'Willow Grove']

In [15]:
buisness[buisness["City"].isin(similar_cities)].sort_values(["stars"],ascending=False).groupby("City").head(3)

business_id                                     name  \
0      Pns2l4eNsfO8kk83dixA6A                 Abby Rappoport, LAC, CMQ   
46128  L4-_gPiqsuX50JN_-qUhNQ  Jeannine’s American Bakery & Restaurant   
44080  i235c6uCPb1b0WlqpYTLHA                        Bliss Connections   
44137  oQiX2J7Qdg7pAIAcqrHNrg                                 Tanoshii   
52585  edl8hfcWimih49t_8vULvw                           Public Storage   
50929  p3eSU2HIgFGULEEj0bvrag                        Express Cleanouts   
57430  MUaiPeFCrVJ_ESYSi5kJ6w    Green Heating & Air Conditioning, LLC   
62848  7a2gaL_UhgIs7DolzHbJ_w                 Frida's Mexican Taqueria   
58010  3aklsYoJN30SZ3_3ORsRxg                       Daniel L Beardsley   

                      address            City         State  postal_code  \
0      1616 Chapala St, Ste 2  Santa  Barbara    California      93101.0   
46128              1 State St  Santa  Barbara    California      93101.0   
44080   3791 State St, Unit D  Santa  Barbara    California      93105.0   
44137             3 Easton Rd    Willow Grove  Pennsylvania      19090.0   
52585        2535 Maryland Rd    Willow Grove  Pennsylvania      19090.0   
50929                     NaN    Willow Grove  Pennsylvania      19090.0   
57430  631 Keller Creamery Rd         Telford  Pennsylvania      18969.0   
62848           133 N Main St         Telford  Pennsylvania      18969.0   
58010            165 Penn Ave         Telford  Pennsylvania      18969.0   

        latitude   longitude  stars  review_count  ...  perms  asian  \
0      34.426679 -119.711197    5.0             7  ...  False  False   
46128  34.412205 -119.689592    5.0            41  ...  False  False   
44080  34.440052 -119.746500    5.0            17  ...  False  False   
44137  40.141473  -75.116797    5.0            36  ...  False  False   
52585  40.161766  -75.127651    5.0             6  ...  False  False   
50929  40.149891  -75.125349    5.0             7  ...  False  False   
57430  40.304062  -75.373460    5.0             7  ...  False  False   
62848  40.325999  -75.329533    5.0             9  ...  False  False   
58010  40.324126  -75.330218    5.0             6  ...  False  False   

      dairy-free gluten-free  vegan kosher  halal soy-free  vegetarian  \
0          False       False  False  False  False    False       False   
46128      False       False  False  False  False    False       False   
44080      False       False  False  False  False    False       False   
44137      False       False  False  False  False    False       False   
52585      False       False  False  False  False    False       False   
50929      False       False  False  False  False    False       False   
57430      False       False  False  False  False    False       False   
62848      False       False  False  False  False    False       False   
58010      False       False  False  False  False    False       False   

      idFoodRelated  
0              True  
46128          True  
44080          True  
44137          True  
52585          True  
50929          True  
57430          True  
62848          True  
58010          True  

[9 rows x 96 columns]

In [172]:
import pickle
import pymongo
from sklearn.metrics.pairwise import cosine_similarity


# Recommend similar cities
class getRecommendations:

    def __init__(self) :

        filtering_datas = pickle.load(open("content_filttering.pkl","rb"))
        self.cities = filtering_datas["cities"]
        self.cos_sim = filtering_datas["cossim"]
        self.reverse_indices = filtering_datas["reverse_indices"]

        client = pymongo.MongoClient("mongodb://localhost:27017")
        self.database = client["tourism_recommendation"]
        self.users = self.database["UserDetails"]
        self.overall_cities = []

    def get_similar_cities(self , city_name):

        try:

            indx = self.reverse_indices[city_name]

            similar_cities = list(enumerate(self.cos_sim[indx]))

            similar_cities = sorted(similar_cities ,key = lambda x : x[1], reverse=True)

            similar_cities = similar_cities[1:11]
            
            city_indices =  [i for i,j in similar_cities]

            self.overall_cities += [self.cities[i] for i in city_indices][1:4]

            print(f"similar cities : {[self.cities[i] for i in city_indices][1:4]}")
        
        except:

            return False
    
    def get_cities_from_similar_users(self,cossim, my_ratings , othes_ratings):

        get_similar_users = list(enumerate(cossim[0]))
        get_similar_users = sorted(get_similar_users ,key = lambda x : x[1], reverse=True)

        cities = []
        t = 0
        while (len(cities) < 4 and t < len(get_similar_users)):

            print(get_similar_users[t])
            user_index = get_similar_users[t][0]
            ratings = othes_ratings[user_index]
                
            for i in range(len(my_ratings)):

                if(ratings[i] >= 3.5 and my_ratings[i] == 2.5):
                    if(self.cities[i] not in cities):
                        cities.append(self.cities[i])
            t+=1
        
        print(f"similar_users_cities : {cities}")

        self.overall_cities +=  cities



    
    def getOverAllRecommendation(self , email) :

        self.overall_cities = []

        mySim = self.users.find_one({"email" : email} , {"_id" : 0 , "search_history" : 1 , "cities_rating":1})

        print(mySim)

        if(mySim == None):

            self.createUser(email)
            return False # False means the user is newUset so recommend Top hotels in out history
        
        recommended_cities = []

        if(len(mySim["search_history"])>0):
            most_occured_city = mySim["search_history"][-1]
            times = 1

            for city in  set(mySim["search_history"][-1:]):

                count = mySim["search_history"].count(city)

                if(count > times):
                    most_occured_city = city
                    times = count
                    
            self.get_similar_cities(most_occured_city)

        self.getSimilarUsers(email,mySim)
            
        print(f"most occured {most_occured_city} count {count}")

        
            
        

    def getSimilarUsers(self , email , mySim):


        if(len(mySim["search_history"]) < 4 ):
            return False # False means the user is newUser and not searched that much . so we recommend Top hotels in out history
        

        otherSim = self.users.find({ "email" : {"$ne" : email}}, {"_id" : 0 , "search_history" : 1 , "cities_rating":1})

        other_users_cities_rating = []

        for l in otherSim:
            other_users_cities_rating.append(l["cities_rating"])

        cossim = cosine_similarity([mySim["cities_rating"]] ,other_users_cities_rating )

        print(cossim)

        self.get_cities_from_similar_users(cossim , mySim["cities_rating"] , other_users_cities_rating)



    def createUser(self, email , total_cities = 1083):

        UserDetails = {"email" : email , "search_history" : [] , "cities_rating" : [2.5]*total_cities}

        x = self.users.insert_one(UserDetails)

        print(str(x) + f"New user {email} has been created")
        
    
    def addHistory(self , email,name):
        mySim = self.users.find_one({"email" : email} , {"_id" : 0 , "search_history" : 1 ,"cities_rating" : 1 })

        if(mySim == None):
            self.createUser(email)
            self.addHistory(email,name)
            return
        
        sr = mySim["search_history"]

        if(name in self.cities):
            sr = sr + [name]

            x = self.users.update_one({"email" : email} , { "$set" : {"search_history" : sr}})
            print(x)

            cr = mySim["cities_rating"]
            city_index = self.reverse_indices[name]
            cr[city_index] += 1
            
            x = self.users.update_one({"email" : email} , { "$set" : {"cities_rating" : cr}})

            return "Search history updated"
        
        return "City not in the list"
    
    
    def updateRating(self , email , rating , name):

        mySim = self.users.find_one({"email" : email} , {"_id" : 0 , "cities_rating" : 1 })

        if(mySim == None):
            self.createUser(email)
            self.updateRating(email,rating ,name)
            return
        
        cr = mySim["cities_rating"]


        
        print(f"cities_rating {cr}")
        if(name in self.cities):
            i = self.reverse_indices[name]
            cr[i] = rating
            x = self.users.update_one({"email" : email} , { "$set" : {"cities_rating" : cr}})
            print(x)
            return "User's rating updated"
        
        return "City not in the list"
        

In [173]:
gt = getRecommendations()

In [174]:
gt.get_similar_cities("AVON")

similar cities : ['Pasadena', 'Oldmans', 'CLEARWATER BEACH']


In [179]:
email1 = "221501080@rajalakshmi.edu.in"
email2 = "221501141@rajalakshmi.edu.in"
email3 = "221501122@rajalakshmi.edu.in"

gt.addHistory(email1,"AVON")
gt.addHistory(email1,"Pasadena")
gt.addHistory(email1,"Oldmans")
gt.addHistory(email1, "CLEARWATER BEACH")

UpdateResult({'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)
UpdateResult({'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)
UpdateResult({'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)
UpdateResult({'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)


'Search history updated'

In [180]:
gt.addHistory(email2,"Algiers")
gt.addHistory(email2,"CLEARWATER BEACH")
gt.addHistory(email2,"Oldmans")
gt.addHistory(email2 , "Corona De Tucson")

UpdateResult({'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)
UpdateResult({'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)
UpdateResult({'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)
UpdateResult({'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)


'Search history updated'

In [183]:
gt.addHistory(email3 , "Chalemette")
gt.addHistory(email3 , "View")
gt.addHistory(email3 , "Pasadena")
gt.addHistory(email3,"AVON")
gt.addHistory(email3,"Upper Southampton Township")

UpdateResult({'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)
UpdateResult({'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)
UpdateResult({'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)
UpdateResult({'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)
UpdateResult({'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)


'Search history updated'

In [184]:
gt.getOverAllRecommendation(email1)

{'search_history': ['AVON', 'Pasadena', 'Oldmans', 'CLEARWATER BEACH', 'AVON', 'Pasadena', 'Oldmans', 'CLEARWATER BEACH'], 'cities_rating': [4.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 4.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5, 2.5,

In [186]:
a = dict()
a.get("hi","oi")

'oi'

In [187]:
len(None)

TypeError: object of type 'NoneType' has no len()